In [1]:
from pyspark.sql import SparkSession #Sesión para uso de spark
import pyspark.sql.functions as F #Funciones spark
import pandas as pd #Tratamiento data

spark = SparkSession.builder.master("local") \
                    .appName('Sales_Analysis') \
                    .getOrCreate()

In [2]:
data=spark.read.csv("../data/raw/Real_Estate_Sales_2001-2020_GL.csv",header=True)

In [3]:
#Actualización de datos
data = (data.withColumn("List Year",F.col("List Year").cast("int")) #Entero
            .withColumn("Date Recorded",F.to_date(F.col("Date Recorded"),"MM/dd/yyyy")) #Tipo Fecha
            .withColumn("Assessed Value",F.col("Assessed Value").cast("int")) #Entero
            .withColumn("Sale Amount",F.col("Sale Amount").cast("float")) #Decimal
            .withColumn("Sales Ratio",F.col("Sales Ratio").cast("float"))) #Decimal

In [6]:
data.show()

+-------------+---------+-------------+------------+--------------------+--------------+-----------+-----------+-------------+----------------+------------+--------------------+-----------+--------------------+
|Serial Number|List Year|Date Recorded|        Town|             Address|Assessed Value|Sale Amount|Sales Ratio|Property Type|Residential Type|Non Use Code|    Assessor Remarks|OPM remarks|            Location|
+-------------+---------+-------------+------------+--------------------+--------------+-----------+-----------+-------------+----------------+------------+--------------------+-----------+--------------------+
|      2020177|     2020|   2021-04-14|     Ansonia|       323 BEAVER ST|        133000|   248400.0|     0.5354|  Residential|   Single Family|        NULL|                NULL|       NULL|POINT (-73.06822 ...|
|      2020225|     2020|   2021-05-26|     Ansonia|      152 JACKSON ST|        110500|   239900.0|     0.4606|  Residential|    Three Family|        NULL|

In [5]:
data_loc=pd.read_excel("../data/raw/FipCodes.xlsx")
data_loc["FIPS"]= "0" + data_loc["FIPS"].astype(str)

In [6]:
# Análisis por county - generación de tabla
df = spark.read.csv("../data/raw/CT_Municipalities.csv", header=True)
df.show()

+--------+--------------------+------------+------------------+--------------------+--------------------+-------------------------------+----------+-----------+----------------+---------------------+-----------------------+--------------------------+----------------------------+--------------------+--------------------+----------------------------+--------------------+-----------+--------------+--------------------+--------------------+--------------------+----------------+----------------+
|OBJECTID|            GlobalID|Municipality|MunicipalityNumber|      PlanningRegion| CouncilOfGovernment|MetropolitanPlanningOrganizatio|    County|DEMHSRegion|StatePoliceTroop|DOTMunicipalityNumber|DOTConstructionDistrict|DOTHighwayOperationsCenter|TransportationManagementArea| OzoneDesignatedArea|  PM25DesignatedArea|CarbonMonoxideDesignatedArea|     TransitDistrict|SquareMiles|  created_user|        created_date|    last_edited_user|    last_edited_date|     Shape__Area|   Shape__Length|
+-------

In [7]:
#Join entre tablas
df_join=data.join(df,on=(data.Town==df.Municipality),how="inner")

In [8]:
df_map=df_join.groupBy("List Year","County").agg(
    F.sum("Assessed Value").alias("Assessed Value"),
    F.sum("Sale Amount").alias("Sale Amount")
).withColumn("Sale Ratio",F.col("Sale Amount")/F.col("Assessed Value"))
df_map.show()

+---------+----------+--------------+--------------------+------------------+
|List Year|    County|Assessed Value|         Sale Amount|        Sale Ratio|
+---------+----------+--------------+--------------------+------------------+
|     2019|New London|     950068634|       1.387127422E9|1.4600286467303794|
|     2020|   Windham|     331605072|     6.65841951875E8|2.0079365730419227|
|     2007|   Windham|     127095938|        2.13057472E8|1.6763515447677013|
|     2011|  Hartford|    1422457244|       1.702242974E9|1.1966918381414633|
|     2009| Middlesex|     518022706|        6.55457644E8|1.2653067836760035|
|     2019|  Hartford|    2666668481|4.2550823606972656E9|1.5956547996178403|
|     2002|   Tolland|     391720676|        6.11228123E8|1.5603672730310514|
|     2018| New Haven|    2618047376|3.4370484847265625E9| 1.312828987066643|
|     2020|New London|    1170107181| 2.207652163109375E9|1.8867093536018347|
|     2001|Litchfield|     445522984|        8.02773823E8|1.8018

In [9]:
#Conversión a pandas para realizar las gráficas
df_map_pd=df_map.toPandas()
df_plot=df_map_pd.merge(data_loc,left_on="County",right_on="CTYNAME")

In [10]:
df_plot

List Year      County  Assessed Value   Sale Amount  Sale Ratio   FIPS  \
0         2019  New London       950068634  1.387127e+09    1.460029  09011   
1         2020  New London      1170107181  2.207652e+09    1.886709  09011   
2         2003  New London       683856667  1.292823e+09    1.890489  09011   
3         2018  New London       784536507  1.148929e+09    1.464468  09011   
4         2013  New London       616645191  7.880679e+08    1.277993  09011   
..         ...         ...             ...           ...         ...    ...   
155       2001   Fairfield      3613878681  6.320145e+09    1.748854  09001   
156       2011   Fairfield      7945099050  6.605744e+09    0.831424  09001   
157       2003   Fairfield      5918342043  9.183981e+09    1.551783  09001   
158       2008   Fairfield      4184604931  4.037745e+09    0.964905  09001   
159       2015   Fairfield      6439333536  5.939272e+09    0.922343  09001   

          STNAME     CTYNAME  TOT_POP  TOT_MALE  ...  NHWA_MALE  NHWA_FEMALE  \
0    Connecticut  New London   274170    136944  ...     105427       107270   
1    Connecticut  New London   274170    136944  ...     105427       107270   
2    Connecticut  New London   274170    136944  ...     105427       107270   
3    Connecticut  New London   274170    136944  ...     105427       107270   
4    Connecticut  New London   274170    136944  ...     105427       107270   
..           ...         ...      ...       ...  ...        ...          ...   
155  Connecticut   Fairfield   933835    455031  ...     296516       313222   
156  Connecticut   Fairfield   933835    455031  ...     296516       313222   
157  Connecticut   Fairfield   933835    455031  ...     296516       313222   
158  Connecticut   Fairfield   933835    455031  ...     296516       313222   
159  Connecticut   Fairfield   933835    455031  ...     296516       313222   

     NHWhite_Alone  Not_NHWhite_Alone  MinorityMinority  MinorityPCT   Black  \
0           212697              61473                No       0.2242   17769   
1           212697              61473                No       0.2242   17769   
2           212697              61473                No       0.2242   17769   
3           212697              61473                No       0.2242   17769   
4           212697              61473                No       0.2242   17769   
..             ...                ...               ...          ...     ...   
155         609738             324097                No       0.3471  110864   
156         609738             324097                No       0.3471  110864   
157         609738             324097                No       0.3471  110864   
158         609738             324097                No       0.3471  110864   
159         609738             324097                No       0.3471  110864   

    BlackPCT  Hispanic  HispanicPCT  
0       0.06     25167       0.0918  
1       0.06     25167       0.0918  
2       0.06     25167       0.0918  
3       0.06     25167       0.0918  
4       0.06     25167       0.0918  
..       ...       ...          ...  
155     0.12    166186       0.1780  
156     0.12    166186       0.1780  
157     0.12    166186       0.1780  
158     0.12    166186       0.1780  
159     0.12    166186       0.1780  

[160 rows x 23 columns]

In [18]:
#Eliminar columnas inncesarias
Not_cols=["STNAME","TOT_POP","CTYNAME","TOT_MALE","TOT_FEMALE",
          "WA_MALE","WA_FEMALE","NHWA_MALE","NHWA_FEMALE","NHWhite_Alone",
          "Not_NHWhite_Alone","MinorityMinority","MinorityPCT","Black",
          "BlackPCT","Hispanic","HispanicPCT"]
df_save=df_plot.copy().drop(columns=Not_cols)
df_save["FIPS"]=df_save["FIPS"].astype("string")
df_save

List Year      County  Assessed Value   Sale Amount  Sale Ratio   FIPS
0         2019  New London       950068634  1.387127e+09    1.460029  09011
1         2020  New London      1170107181  2.207652e+09    1.886709  09011
2         2003  New London       683856667  1.292823e+09    1.890489  09011
3         2018  New London       784536507  1.148929e+09    1.464468  09011
4         2013  New London       616645191  7.880679e+08    1.277993  09011
..         ...         ...             ...           ...         ...    ...
155       2001   Fairfield      3613878681  6.320145e+09    1.748854  09001
156       2011   Fairfield      7945099050  6.605744e+09    0.831424  09001
157       2003   Fairfield      5918342043  9.183981e+09    1.551783  09001
158       2008   Fairfield      4184604931  4.037745e+09    0.964905  09001
159       2015   Fairfield      6439333536  5.939272e+09    0.922343  09001

[160 rows x 6 columns]

In [19]:
df_save.to_csv("../data/processed/CT_Municipalities.csv",index=False)

In [21]:
df_try=pd.read_csv("../data/processed/CT_Municipalities.csv",dtype={'FIPS': object})
df_try

List Year      County  Assessed Value   Sale Amount  Sale Ratio   FIPS
0         2019  New London       950068634  1.387127e+09    1.460029  09011
1         2020  New London      1170107181  2.207652e+09    1.886709  09011
2         2003  New London       683856667  1.292823e+09    1.890489  09011
3         2018  New London       784536507  1.148929e+09    1.464468  09011
4         2013  New London       616645191  7.880679e+08    1.277993  09011
..         ...         ...             ...           ...         ...    ...
155       2001   Fairfield      3613878681  6.320145e+09    1.748854  09001
156       2011   Fairfield      7945099050  6.605744e+09    0.831424  09001
157       2003   Fairfield      5918342043  9.183981e+09    1.551783  09001
158       2008   Fairfield      4184604931  4.037745e+09    0.964905  09001
159       2015   Fairfield      6439333536  5.939272e+09    0.922343  09001

[160 rows x 6 columns]

In [7]:
df_map_2=data.groupBy("List Year","Town").agg(
    F.sum("Assessed Value").alias("Assessed Value"),
    F.sum("Sale Amount").alias("Sale Amount")
).withColumn("Sale Ratio",F.col("Sale Amount")/F.col("Assessed Value"))
df_map_2.show()

+---------+-----------+--------------+----------------+------------------+
|List Year|       Town|Assessed Value|     Sale Amount|        Sale Ratio|
+---------+-----------+--------------+----------------+------------------+
|     2020|    Meriden|     179938379|    3.34881028E8|1.8610872781064678|
|     2005|    Windsor|     123355940|    2.23790039E8| 1.814181295201512|
|     2010|    Meriden|      93306661|    1.07237768E8|1.1493045282158365|
|     2014|     Groton|     167888200|    1.59948391E8|0.9527077602833314|
|     2017|    Bethany|      17674120|     2.5492499E7|1.4423631275559972|
|     2017|    Madison|     158705500|    2.09893918E8|1.3225371395446281|
|     2006|New Milford|     139979108|    2.33987316E8|1.6715874200312806|
|     2007|   Scotland|       2631190|       4661400.0| 1.771593841569784|
|     2019|New Milford|     122827401|1.853007760625E8| 1.508627346617063|
|     2010|    Seymour|      32969380|     3.8922617E7|1.1805686670480307|
|     2011|       Lyme|  

In [11]:
df_fin=df_map_2.toPandas()

In [22]:
df_fin.to_csv("../data/processed/CT_Towns.csv",index=False)

In [9]:
from urllib.request import urlopen #Cargado de información en línea
import json #Análisis de archivos Json
#Ajustes para agregar mapa
#Cargado de información externa
with urlopen('https://raw.githubusercontent.com/HandsOnDataViz/ct-boundaries/main/ct-towns-2021-datactgov.geojson') as response:
    counties = json.load(response)

In [20]:
import plotly.express as px #Graficación de mapas

fig = px.choropleth_mapbox(df_fin[df_fin["List Year"]==2008], geojson=counties, locations='Town', color='Sale Ratio',
                           color_continuous_scale="Viridis",
                           featureidkey="properties.town",
                           #range_color=(0, 12),
                           labels={'TOT_POP':'Población',
                                   'TOT_MALE' : "Número Hombres"},
                           center={"lat": 41.599998, "lon": -72.699997},
                           mapbox_style="carto-positron"
                          )
fig.update_layout(margin={"r":0,"t":0,"l":0,"b":0})
fig.show()